**Import Python libraries for data analysis and machine learning.**  
Including Pandas, Numpy, Plotly, Pmdarima, Matplotlib, Scikit-Learn, Seaborn and LightGBM.

In [1]:
import time
import warnings
import os
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import lightgbm as lgb
import statsmodels.api as sm
import pmdarima as pm
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import r2_score
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import mean_squared_error
from plotly.subplots import make_subplots



**Define Python functions and data preprocessing steps** for computing realized volatility, log returns, and filtering warnings.   
The code also loads train.csv, order_book_feature.parquet, and trades.parquet, and applies log returns to the order book feature data.

In [2]:
warnings.filterwarnings('ignore')

def rmspe(y_true, y_pred):
    return  (np.sqrt(np.mean(np.square((y_true - y_pred) / y_true))))

def log_return(list_stock_prices):
    return np.log(list_stock_prices).diff() 

def realized_volatility(series_log_return):
    return np.sqrt(np.sum(series_log_return**2))

def realized_volatility_per_time_id(df_book_data):
    df_book_data['log_return'] = df_book_data.groupby(['time_id','stock_id'])['wap'].apply(log_return)
    df_book_data = df_book_data[~df_book_data['log_return'].isnull()]
    df_realized_vol_per_stock =  pd.DataFrame(df_book_data.groupby(['stock_id','time_id'])['log_return'].agg(realized_volatility)).reset_index()
    df_realized_vol_per_stock = df_realized_vol_per_stock.rename(columns = {'log_return':'prediction'})
    return df_realized_vol_per_stock

train = pd.read_csv('train.csv')
book = pd.read_parquet('order_book_feature.parquet')
trade =  pd.read_parquet('trades.parquet')
book['wap'] = (book['bid_price1'] * book['ask_size1'] +
                                book['ask_price1'] * book['bid_size1']) / (
                                       book['bid_size1']+ book['ask_size1'])
book['log_return'] = book.groupby(['time_id','stock_id'])['wap'].apply(log_return)
book.head()

stock_id  time_id  seconds_in_bucket  bid_price1  ask_price1  bid_price2  \
0      8382       12                1.0      722.17      722.63      722.15   
1      8382       12                2.0      722.18      722.88      722.17   
2      8382       12                3.0      722.33      722.65      722.27   
3      8382       12                4.0      722.68      722.98      722.48   
4      8382       12                5.0      722.52      722.96      722.42   

   ask_price2  bid_size1  ask_size1  bid_size2  ask_size2         wap  \
0      722.64        100         25         25         20  722.538000   
1      722.98         25         10         66        100  722.680000   
2      722.74         25        120        200         25  722.385172   
3      723.00         25        100         25          1  722.740000   
4      722.97        125         20          3        110  722.899310   

   log_return  
0         NaN  
1    0.000197  
2   -0.000408  
3    0.000491  
4    0.000220

**EWMA prediction model:**   
Calculating the exponentially weighted moving average volatility of a stock and merging it with a training dataset, with time tracking.

In [3]:
start = time.time()
def calc_volatility(group):
    if 'log_return' not in group.columns:
        return np.nan
    ewm_vol = group['log_return'].ewm(span=10).std() * np.sqrt(len(group))
    return ewm_vol.mean()

volatility = book.groupby(['time_id', 'stock_id']).apply(calc_volatility).reset_index(name='prediction_ewma')
train = train.merge(volatility, on=['time_id', 'stock_id'], how='left')
end = time.time()
print('Predicate takes:',(end-start), 'sec')

Predicate takes: 11.165237188339233 sec


**Evaluation metrics for the EWMA prediction model.**  
Including R2 score, root-mean-squared-percentage-error (RMSPE), mean absolute error (MAE), and root-mean-squared error (RMSE).

In [4]:
R2_ewma = round(r2_score(y_true = train['target'], y_pred = train['prediction_ewma']),3)
RMSPE_ewma = round(rmspe(y_true = train['target'], y_pred = train['prediction_ewma']),3)
MAE_ewma = np.mean(np.abs(train['target'] - train['prediction_ewma']))
RMSE_ewma = mean_squared_error(y_true = train['target'], y_pred = train['prediction_ewma'], squared=False)
print(f'Performance of the ewma prediction: R2 score: {R2_ewma}, RMSPE: {RMSPE_ewma}, MAE: {MAE_ewma}, RMSE: {RMSE_ewma}')


Performance of the ewma prediction: R2 score: 0.872, RMSPE: 0.188, MAE: 0.0005919049499575599, RMSE: 0.0009021313768584449


**Scatter plot with regression line to compare actual vs. predicted volatility for all stocks.**  
The regression line helps visualize the overall relationship between the actual and predicted values. The transparency (alpha) of the scatter points is set to 0.3, making it easier to see overlapping points.

In [5]:
# Remove rows with NaN predictions
train_filtered = train.dropna(subset=['prediction_ewma'])

# Create a scatter plot with a regression line
fig = px.scatter(train_filtered, x='target', y='prediction_ewma', trendline='ols', title='Actual vs. Predicted Volatility for All Stocks (EWMA)', opacity=0.3)

# Customize the chart
fig.update_xaxes(title='Actual Target Volatility')
fig.update_yaxes(title='Predicted Volatility')

# Update the trendline color, style, and width
fig.update_traces(line=dict(color='red', width=2, dash='dash'), selector=dict(type='scatter', mode='lines'))

fig.show()

**Data visualization for comparing actual vs. predicted volatility of stocks over time using Python's Matplotlib library.**  
The actual target volatility is plotted in blue, while the predicted volatility is plotted in orange. The legend helps differentiate between the actual and predicted values.

In [6]:
# Group the data by time_id and calculate the mean target and prediction for each group
mean_values_per_time_id = train_filtered.groupby('time_id').mean()[['target', 'prediction_ewma']]

# Create a line chart comparing the actual target and predicted volatility
fig = px.line(mean_values_per_time_id, x=mean_values_per_time_id.index, y=mean_values_per_time_id.columns,
              labels={'value': 'Volatility', 'variable': 'Type', 'time_id': 'Time ID'}, title='Actual vs. Predicted Volatility for All Stocks (EWMA)')

# Customize the chart
fig.update_xaxes(title='Time ID')
fig.update_yaxes(title='Volatility')
fig.show()

**LightGBM model:**  
This code implements a stock volatility prediction model using LightGBM, a gradient boosting framework that uses tree-based learning algorithms.  
The code starts by defining a list of stock IDs to be analyzed. Then, it loops through each stock ID and performs the following steps:  
1. Selects the training data for the current stock ID.
2. Prepares the data for the LightGBM model by calculating the realized volatility for each time ID and splitting the data into training and testing sets.
3. Trains a LightGBM model with the training data.
4. Predicts the volatility for each time ID using the trained model.
5. Inserts the prediction results into the original training dataframe.  

Finally, the code prints the total time taken to execute the entire process.

In [7]:
stock_ids = [9323, 22675, 22951, 22729, 48219, 22753, 22771, 104919, 50200, 8382]

start = time.time()
for stock_id in stock_ids:
    train_stock = train[train["stock_id"] == stock_id]
    train_stock['prediction'] = np.nan

    # Prepare data for the LightGBM model
    book_stock = book[book['stock_id'] == stock_id]
    book_stock['log_return_squared'] = book_stock['log_return']**2
    book_stock_agg = book_stock.groupby(['time_id']).agg(
        {'log_return_squared': ['sum', 'count']}).reset_index()
    book_stock_agg.columns = ['time_id', 'log_return_squared_sum', 'log_return_count']
    book_stock_agg['realized_volatility'] = np.sqrt(book_stock_agg['log_return_squared_sum'])

    # Prepare the dataset for training and testing
    X = book_stock_agg[['log_return_squared_sum', 'log_return_count']].values
    y = book_stock_agg['realized_volatility'].values
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Train a LightGBM model
    lgb_train = lgb.Dataset(X_train, y_train)
    lgb_eval = lgb.Dataset(X_test, y_test, reference=lgb_train)
    params = {
        'boosting_type': 'gbdt',
        'objective': 'regression',
        'metric': 'rmse',
        'num_leaves': 31,
        'learning_rate': 0.05,
        'feature_fraction': 0.9,
        'bagging_fraction': 0.8,
        'bagging_freq': 5,
        'verbose': -1,
        'force_col_wise': True
    }
    gbm = lgb.train(params, lgb_train, num_boost_round=40, valid_sets=lgb_eval, early_stopping_rounds=5, verbose_eval=False)

    # Predict volatility using the trained LightGBM model
    train_stock = train_stock.merge(book_stock_agg[['time_id', 'log_return_squared_sum', 'log_return_count']], on='time_id')
    train_stock['prediction'] = gbm.predict(train_stock[['log_return_squared_sum', 'log_return_count']].values, num_iteration=gbm.best_iteration)
    
    # Insert prediction results into the train dataframe
    for index, row in train_stock.iterrows():
        train.loc[(train['time_id'] == row['time_id']) & (train['stock_id'] == stock_id), 'prediction_lgb'] = row['prediction']
end = time.time()
print('Predicate takes:',(end-start), 'sec')

Predicate takes: 8.958562135696411 sec


**Evaluation metrics for the LightGBM Model,**  
Including R2 score, root-mean-squared-percentage-error (RMSPE), mean absolute error (MAE), and root-mean-squared error (RMSE).

In [8]:
R2_lgb = round(r2_score(y_true = train['target'], y_pred = train['prediction_lgb']),3)
RMSPE_lgb = round(rmspe(y_true = train['target'], y_pred = train['prediction_lgb']),3)
MAE_lgb = np.mean(np.abs(train['target'] - train['prediction_lgb']))
RMSE_lgb = mean_squared_error(y_true = train['target'], y_pred = train['prediction_lgb'], squared=False)
print(f'Performance of the lgb prediction: R2 score: {R2_lgb}, RMSPE: {RMSPE_lgb}, MAE: {MAE_lgb}, RMSE: {RMSE_lgb}')

Performance of the lgb prediction: R2 score: 0.866, RMSPE: 0.21, MAE: 0.0006255724380403265, RMSE: 0.000922521090872939


**Scatter plot with regression line to compare actual vs. predicted volatility for all stocks.**  
A scatter plot with regression lines for each stock, comparing the actual volatility (target) and the predicted volatility (prediction_lgb).

In [9]:
# Remove rows with NaN predictions
train_filtered = train.dropna(subset=['prediction_lgb'])
# Create a scatter plot with a regression line
# Create a scatter plot with a regression line
fig = px.scatter(train_filtered, x='target', y='prediction_lgb', trendline='ols', title='Actual vs. Predicted Volatility for All Stocks (LightGBM)', opacity=0.3)

# Customize the chart
fig.update_xaxes(title='Actual Target Volatility')
fig.update_yaxes(title='Predicted Volatility')
fig.show()


In [10]:
# Group the data by time_id and calculate the mean target and prediction for each group
mean_values_per_time_id = train_filtered.groupby('time_id').mean()[['target', 'prediction_lgb']]

# Create a line chart comparing the actual target and predicted volatility
fig = px.line(mean_values_per_time_id, x=mean_values_per_time_id.index, y=mean_values_per_time_id.columns,
              labels={'value': 'Volatility', 'variable': 'Type', 'time_id': 'Time ID'}, title='Actual vs. Predicted Volatility for All Stocks (LightGBM)')

# Customize the chart
fig.update_xaxes(title='Time ID')
fig.update_yaxes(title='Volatility')
fig.show()

**Calculation and Insertion of RMSE for EWMA and LGB Models.**  
This code creates a summary dataframe with columns for stock IDs, RMSE for EWMA model, and RMSE for LGB model, initializes the RMSE values to zero. The code then calculates the RMSE for each stock's predictions using both models, and inserts the results into the summary dataframe using a loop over the summary dataframe's rows.

In [11]:
summary = pd.DataFrame()
summary['stock_id'] = stock_ids
summary['RMSE_ewma'] = 0
summary['RMSE_lgb'] = 0

In [12]:
for stock_id in stock_ids:
    train_stock = train[train["stock_id"] == stock_id]
    RMSE = mean_squared_error(y_true = train_stock['target'], y_pred = train_stock['prediction_ewma'], squared=False)
     #insert prediction results into train dataframe
    for index, row in summary.iterrows():
        summary.loc[((summary['stock_id'] == stock_id), 'RMSE_ewma')] = RMSE
    RMSE = mean_squared_error(y_true = train_stock['target'], y_pred = train_stock['prediction_lgb'], squared=False)
     #insert prediction results into train dataframe
    for index, row in summary.iterrows():
        summary.loc[((summary['stock_id'] == stock_id), 'RMSE_lgb')] = RMSE

**Hybrid Model prediction.**  
This code computes the Bayesian Averaging of Exponentially Weighted Moving Average (EWMA) and LightGBM (LGB) predictions for each stock in the train dataset using a provided equation.  
The resulting predictions are stored in a new 'prediction_hybrid' column, which is then cleaned up by dropping the 'RMSE_ewma' and 'RMSE_lgb' columns.

In [13]:
start = time.time()
train['prediction_hybrid'] = 0
merged_df = train.merge(summary, on='stock_id')
# Compute the prediction_hybrid column using the provided equation
merged_df['prediction_hybrid'] = ((1 - merged_df['RMSE_ewma']) * merged_df['prediction_ewma'] +(1 - merged_df['RMSE_lgb']) * merged_df['prediction_lgb']) / ((1 - merged_df['RMSE_ewma']) + (1 - merged_df['RMSE_lgb']))

# Clean up the merged DataFrame
final_df = merged_df.drop(columns=['RMSE_ewma', 'RMSE_lgb'])
        
end = time.time()
print('Predicate takes:',(end-start), 'sec')
merged_df

Predicate takes: 0.012644529342651367 sec


time_id  stock_id    target  prediction_ewma  prediction_lgb  \
0           12      8382  0.008714         0.010480        0.010615   
1           13      8382  0.006838         0.007318        0.007742   
2           14      8382  0.005098         0.006124        0.006783   
3           15      8382  0.004095         0.004606        0.005457   
4           16      8382  0.004646         0.003837        0.004523   
...        ...       ...       ...              ...             ...   
11515     1195    104919  0.001092         0.001398        0.001557   
11516     1196    104919  0.001147         0.001042        0.001233   
11517     1197    104919  0.001124         0.001007        0.001197   
11518     1198    104919  0.001499         0.001440        0.001612   
11519     1199    104919  0.002154         0.001396        0.001565   

       prediction_hybrid  RMSE_ewma  RMSE_lgb  
0               0.010547   0.001321  0.001453  
1               0.007530   0.001321  0.001453  
2               0.006454   0.001321  0.001453  
3               0.005032   0.001321  0.001453  
4               0.004180   0.001321  0.001453  
...                  ...        ...       ...  
11515           0.001478   0.000453  0.000462  
11516           0.001138   0.000453  0.000462  
11517           0.001102   0.000453  0.000462  
11518           0.001526   0.000453  0.000462  
11519           0.001480   0.000453  0.000462  

[11520 rows x 8 columns]

**Evaluation metrics for the Hybrid Model**  
Including R2 score, root-mean-squared-percentage-error (RMSPE), mean absolute error (MAE), and root-mean-squared error (RMSE).

In [14]:
R2_hybrid = round(r2_score(y_true = final_df['target'], y_pred = final_df['prediction_hybrid']),3)
RMSPE_hybrid = round(rmspe(y_true = final_df['target'], y_pred = final_df['prediction_hybrid']),3)
MAE_hybrid = np.mean(np.abs(final_df['target'] - final_df['prediction_hybrid']))
RMSE_hybrid = mean_squared_error(y_true = final_df['target'], y_pred = final_df['prediction_hybrid'], squared=False)
print(f'Performance of the hybrid prediction: R2 score: {R2_hybrid}, RMSPE: {RMSPE_hybrid}, MAE: {MAE_hybrid}, RMSE: {RMSE_hybrid}')

Performance of the hybrid prediction: R2 score: 0.878, RMSPE: 0.19, MAE: 0.0005876376322791933, RMSE: 0.0008814628852089496


**Scatter plot with regression line to compare actual and predicted volatility.**  
Creating a scatter plot with a regression line to visualize the relationship between actual and predicted volatility.

In [15]:
# Scatter plot with regression line
fig = px.scatter(final_df, x='target', y='prediction_hybrid', opacity=0.5)

# Add regression line
m, b = np.polyfit(final_df['target'], final_df['prediction_hybrid'], 1)
x_range = np.linspace(final_df['target'].min(), final_df['target'].max(), 100)
fig.add_scatter(x=x_range, y=m * x_range + b, mode='lines', line=dict(color='red'))

fig.update_layout(
    title='Actual vs. Predicted Volatility (Hybrid)',
    xaxis_title='Actual Volatility',
    yaxis_title='Predicted Volatility'
)
fig.show()

In [16]:
# Group the data by time_id and calculate the mean target and prediction for each group
mean_values_per_time_id =final_df.groupby('time_id').mean()[['target', 'prediction_hybrid']]

# Create a line chart comparing the actual target and predicted volatility
fig = px.line(mean_values_per_time_id, x=mean_values_per_time_id.index, y=mean_values_per_time_id.columns,
              labels={'value': 'Volatility', 'variable': 'Type', 'time_id': 'Time ID'}, title='Actual vs. Predicted Volatility for All Stocks (Hybrid)')

# Customize the chart
fig.update_xaxes(title='Time ID')
fig.update_yaxes(title='Volatility')
fig.show()

**Visualizing Actual vs. Predicted Volatility of Stocks Over Time with Plotly**  
This code prepares data by melting it and then visualizes the comparison between actual and predicted volatility of stocks over time using Plotly line chart with facet rows for actual vs. predicted volatility and color-coded by stock id.

In [17]:
# Preparing data for Plotly visualization
melted_data = pd.melt(final_df, id_vars=['time_id', 'stock_id'], value_vars=['target', 'prediction_hybrid'], 
                      var_name='Variable', value_name='Volatility')

# Data visualization for comparing actual vs. predicted volatility over time
fig = px.line(melted_data, x='time_id', y='Volatility', color='stock_id', facet_row='Variable', 
              labels={'time_id': 'Time ID', 'Volatility': 'Volatility', 'Variable': 'data'},
              title='Actual vs. Predicted Volatility of Stocks Over Time (Hybrid)')
fig.show()


In [18]:
final_df['residuals_hybrid'] = final_df['target'] - final_df['prediction_hybrid']

# Plot residuals with a red horizontal line at zero
fig = px.scatter(final_df, x='prediction_hybrid', y='residuals_hybrid', opacity=0.3)
fig.update_layout(
    title='Residuals vs. Predicted Volatility (Hybrid Model)',
    xaxis_title='Predicted Volatility',
    yaxis_title='Residuals',
    shapes=[dict(type='line', y0=0, y1=0, x0=min(final_df['prediction_hybrid']), x1=max(final_df['prediction_hybrid']), yref='y', xref='x', line=dict(color='red'))]
)
fig.show()

# Plot heteroskedasticity with a red Lowess line
fig = px.scatter(final_df, x='prediction_hybrid', y=final_df['residuals_hybrid'] ** 2, opacity=0.3)

lowess = sm.nonparametric.lowess
lowess_line = lowess(final_df['residuals_hybrid'] ** 2, final_df['prediction_hybrid'], frac=0.3)

fig.add_scatter(x=lowess_line[:, 0], y=lowess_line[:, 1], mode='lines', line=dict(color='red'))
fig.update_layout(
    title='Heteroskedasticity Plot (Hybrid Model)',
    xaxis_title='Predicted Volatility',
    yaxis_title='Squared Residuals'
)
fig.show()


In [19]:
performence = pd.DataFrame()

performence['Model'] = 0
performence['R2'] = 0
performence['RMSPE'] = 0
performence = performence.append({'Model':'Naive', 'R2':0.845, 'RMSPE':0.21},ignore_index=True)
performence = performence.append({'Model':'EWMA', 'R2':R2_ewma, 'RMSPE':RMSPE_ewma},ignore_index=True)
performence = performence.append({'Model':'LightGBM', 'R2':R2_lgb, 'RMSPE':RMSPE_lgb},ignore_index=True)
performence = performence.append({'Model':'Hybrid', 'R2':R2_hybrid, 'RMSPE':RMSPE_hybrid},ignore_index=True)
#performence = performence.append({'Model':'ARIMA', 'R2':R2_hybrid, 'RMSPE':RMSPE_hybrid},ignore_index=True)
#performence = performence.append({'Model':'Random Forest', 'R2':R2_hybrid, 'RMSPE':RMSPE_hybrid},ignore_index=True)



# Create the scatter plot
fig = px.scatter(performence, x='R2', y='RMSPE', text='Model', title='Model Performance Comparison')

# Customize the chart
fig.update_traces(textposition='top center')
fig.update_xaxes(title='R2')
fig.update_yaxes(title='RMSPE')

# Add annotations
fig.add_annotation(
    x=0.95,
    y=0.05,
    xref="paper",
    yref="paper",
    text="Better →",
    showarrow=False,
    font=dict(size=14),
    align="left",
    ax=0,
    ay=0,
    bgcolor="rgba(255, 255, 255, 0.9)",
    borderpad=4
)

fig.add_annotation(
    x=0.05,
    y=0.95,
    xref="paper",
    yref="paper",
    text="←Worse",
    showarrow=False,
    font=dict(size=14),
    align="left",
    ax=0,
    ay=0,
    bgcolor="rgba(255, 255, 255, 0.9)",
    borderpad=4
)

fig.show()